In [15]:
from pathlib import Path
import librosa
import torch
from argparse import ArgumentParser
import matplotlib
import h5py
import tqdm
from IPython.display import Audio, display

import numpy as np

import sys
sys.path += ['../music-translation/src']

import utils
import wavenet_models
from utils import save_audio
from wavenet import WaveNet
from wavenet_generator import WavenetGenerator
from nv_wavenet_generator import NVWavenetGenerator
from nv_wavenet_generator import Impl
from scipy.io import wavfile

In [2]:
encoded = []
for directory in Path('encoded-musicnet/encoded').iterdir():
    for path in directory.iterdir():
        encoded += [torch.load(path)]
encoded = torch.cat(encoded, dim=0)

In [3]:
max_val = torch.max(encoded).item()
min_val = torch.min(encoded).item()

mean = torch.mean(encoded).item()
diffs = encoded - mean
var = torch.mean(torch.pow(diffs, 2.0)).item()
print("max", max_val)
print("min", min_val)
print("mean", mean)
print("var", var)

max 2.077653408050537
min -1.7897802591323853
mean -0.008956626988947392
var 0.06574355810880661


In [4]:
noise_vectors = []
for i in range(3):
    noise = np.random.normal(mean, var**0.5, (1, 64, 200))
    noise = torch.from_numpy(noise)
    noise_vectors += [noise]

In [5]:
checkpoint = Path('../music-translation/checkpoints/pretrained_musicnet/bestmodel')
decoders = [0, 1, 2, 3, 4, 5]
batch_size = 1
rate = 16000
split_size = 20



def disp(x, decoder_ix):
    wav = utils.inv_mu_law(x.cpu().numpy())
    print(f'Decoder: {decoder_ix}')
    print(f'X min: {x.min()}, max: {x.max()}')

    display(Audio(wav.squeeze(), rate=rate))
        
def extract_id(path):
    decoder_id = str(path)[:-4].split('_')[-1]
    return int(decoder_id)



print('Starting')
matplotlib.use('agg')

checkpoints = checkpoint.parent.glob(checkpoint.name + '_*.pth')
checkpoints = [c for c in checkpoints if extract_id(c) in decoders]
assert len(checkpoints) >= 1, "No checkpoints found."

model_args = torch.load(checkpoint.parent / 'args.pth')[0]

decoders = []
decoder_ids = []
for checkpoint in checkpoints:
    decoder = WaveNet(model_args)
    decoder.load_state_dict(torch.load(checkpoint)['decoder_state'])
    decoder.eval()
    decoder = decoder.cuda()
    decoder = WavenetGenerator(decoder, batch_size, wav_freq=rate)
    
    decoders += [decoder]
    decoder_ids += [extract_id(checkpoint)]

Starting


In [6]:
yy = {}
with torch.no_grad():
    zz = []
    for vector in noise_vectors:
        zz += [vector]
    zz = torch.cat(zz, dim=0).float().cuda()
    print(zz.shape)

    with utils.timeit("Generation timer"):
        for i, decoder_id in enumerate(decoder_ids):
            yy[decoder_id] = []
            decoder = decoders[i]
            for zz_batch in torch.split(zz, batch_size):
                print(zz_batch.shape)
                splits = torch.split(zz_batch, split_size, -1)
                audio_data = []
                decoder.reset()
                for cond in tqdm.tqdm_notebook(splits):
                    audio_data += [decoder.generate(cond).cpu()]
                audio_data = torch.cat(audio_data, -1)
                yy[decoder_id] += [audio_data]
            yy[decoder_id] = torch.cat(yy[decoder_id], dim=0)

torch.Size([3, 64, 200])
torch.Size([1, 64, 200])


/home/wangjim19/virtualenv/lib/python3.6/site-packages/ipykernel_launcher.py:18: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


Generating:   0%|          | 0/20 [00:00<?, ?it/s]../music-translation/src/wavenet_generator.py:104: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  probabilities = F.softmax(prediction)
Generating: 100%|██████████| 20/20 [08:51<00:00, 26.55s/it]


torch.Size([1, 64, 200])


Generating: 100%|██████████| 20/20 [08:37<00:00, 25.90s/it]

...


torch.Size([1, 64, 200])


Generating: 100%|██████████| 20/20 [09:23<00:00, 28.18s/it]



torch.Size([1, 64, 200])


Generating: 100%|██████████| 20/20 [09:29<00:00, 28.48s/it]


Generation timer took 95904656.8095684 ms


In [22]:
for decoder_ix, decoder_result in yy.items():
    i=1
    for sample_result, noise_vector in zip(decoder_result, noise_vectors):
        disp(sample_result, decoder_ix)
        wav = utils.inv_mu_law(sample_result.cpu().numpy())
        save_audio(wav.squeeze(), Path("results/noise_d" + str(decoder_ix) + "-" + str(i) + ".wav"), rate)
        i++

Decoder: 3
X min: 42, max: 211


Decoder: 3
X min: 44, max: 210


Decoder: 3
X min: 49, max: 207


Decoder: 2
X min: 54, max: 202


Decoder: 2
X min: 55, max: 202


...

Decoder: 5
X min: 9, max: 252


Decoder: 5
X min: 10, max: 254


Decoder: 4
X min: 10, max: 242


Decoder: 4
X min: 19, max: 235


Decoder: 4
X min: 17, max: 239
